# 집값 예측 경진 대회

> feature
- id : 데이터 고유 id
- OverallQual : 전반적 재료와 마감 품질
- YearBuilt : 완공 연도
- YearRemodAdd : 리모델링 연도
- ExterQual : 외관 재료 품질
- BsmtQual : 지하실 높이
- TotalBsmtSF : 지하실 면적 
- 1stFlrSF : 1층 면적 
- GrLivArea : 지상층 생활 면적
- FullBath : 지상층 화장실 개수 
- KitchenQual : 부억 품질 
- GarageYrBlt : 차고 완공 연도
- GarageCars: 차고 자리 개수
- GarageArea: 차고 면적 

> target
- target : 집값(달러 단위)

In [42]:
import os
import sys
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib

In [43]:
train = pd.read_csv('train.csv', encoding='utf-8')
train = train.drop('id',axis=1)
train

Overall Qual  Gr Liv Area Exter Qual  Garage Cars  Garage Area  \
0               10         2392         Ex            3          968   
1                7         1352         Gd            2          466   
2                5          900         TA            1          288   
3                5         1174         TA            2          576   
4                7         1958         Gd            3          936   
...            ...          ...        ...          ...          ...   
1345             6         1756         Gd            2          422   
1346             9         2748         Gd            3          850   
1347             5         1214         TA            1          318   
1348             5          894         TA            2          440   
1349             5          907         TA            1          343   

     Kitchen Qual  Total Bsmt SF  1st Flr SF Bsmt Qual  Full Bath  Year Built  \
0              Ex           2392        2392        Ex          2        2003   
1              Gd           1352        1352        Ex          2        2006   
2              TA            864         900        TA          1        1967   
3              Gd            680         680        TA          1        1900   
4              Gd           1026        1026        Gd          2        2005   
...           ...            ...         ...       ...        ...         ...   
1345           TA            872         888        Ex          2        1996   
1346           Ex           1850        1850        Ex          2        2006   
1347           TA           1214        1214        TA          2        1967   
1348           TA            864         894        Gd          1        1974   
1349           TA            907         907        Gd          1        1978   

      Year Remod/Add  Garage Yr Blt  target  
0               2003           2003  386250  
1               2007           2006  194000  
2               1967           1967  123000  
3               2006           2000  135000  
4               2005           2005  250000  
...              ...            ...     ...  
1345            1997           1996  204000  
1346            2006           2006  390000  
1347            1967           1967  143000  
1348            1974           1974  131000  
1349            1978           1978  140000  

[1350 rows x 14 columns]

In [44]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1350 entries, 0 to 1349
Data columns (total 14 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   Overall Qual    1350 non-null   int64 
 1   Gr Liv Area     1350 non-null   int64 
 2   Exter Qual      1350 non-null   object
 3   Garage Cars     1350 non-null   int64 
 4   Garage Area     1350 non-null   int64 
 5   Kitchen Qual    1350 non-null   object
 6   Total Bsmt SF   1350 non-null   int64 
 7   1st Flr SF      1350 non-null   int64 
 8   Bsmt Qual       1350 non-null   object
 9   Full Bath       1350 non-null   int64 
 10  Year Built      1350 non-null   int64 
 11  Year Remod/Add  1350 non-null   int64 
 12  Garage Yr Blt   1350 non-null   int64 
 13  target          1350 non-null   int64 
dtypes: int64(11), object(3)
memory usage: 147.8+ KB


In [45]:
train.isna().sum()

Overall Qual      0
Gr Liv Area       0
Exter Qual        0
Garage Cars       0
Garage Area       0
Kitchen Qual      0
Total Bsmt SF     0
1st Flr SF        0
Bsmt Qual         0
Full Bath         0
Year Built        0
Year Remod/Add    0
Garage Yr Blt     0
target            0
dtype: int64

# 1. EDA

> EDA 목록
- 
- pandas_profiling 으로 전체 한눈에 보기 

In [46]:
import pandas_profiling
profile = train.profile_report()


In [47]:
profile

Render HTML: 100%|██████████| 1/1 [00:05<00:00,  5.38s/it]


In [48]:
profile.to_file('./profile_report.html')

Export report to file: 100%|██████████| 1/1 [00:00<00:00, 17.86it/s]


In [49]:
# 전체적으로 높은 상관관계
train.corr()

Overall Qual  Gr Liv Area  Garage Cars  Garage Area  \
Overall Qual        1.000000     0.588243     0.571066     0.517218   
Gr Liv Area         0.588243     1.000000     0.516287     0.480863   
Garage Cars         0.571066     0.516287     1.000000     0.840054   
Garage Area         0.517218     0.480863     0.840054     1.000000   
Total Bsmt SF       0.509058     0.419220     0.466017     0.499634   
1st Flr SF          0.476398     0.522535     0.445017     0.485843   
Full Bath           0.554248     0.612423     0.513078     0.418852   
Year Built          0.582875     0.232281     0.505803     0.445816   
Year Remod/Add      0.579142     0.315723     0.433307     0.364369   
Garage Yr Blt       0.553927     0.261861     0.562320     0.536310   
target              0.810607     0.742061     0.634497     0.617151   

                Total Bsmt SF  1st Flr SF  Full Bath  Year Built  \
Overall Qual         0.509058    0.476398   0.554248    0.582875   
Gr Liv Area          0.419220    0.522535   0.612423    0.232281   
Garage Cars          0.466017    0.445017   0.513078    0.505803   
Garage Area          0.499634    0.485843   0.418852    0.445816   
Total Bsmt SF        1.000000    0.868811   0.367648    0.403767   
1st Flr SF           0.868811    1.000000   0.370299    0.290443   
Full Bath            0.367648    0.370299   1.000000    0.508745   
Year Built           0.403767    0.290443   0.508745    1.000000   
Year Remod/Add       0.265506    0.236692   0.472537    0.616008   
Garage Yr Blt        0.347908    0.259898   0.498692    0.815615   
target               0.664047    0.646843   0.554453    0.546037   

                Year Remod/Add  Garage Yr Blt    target  
Overall Qual          0.579142       0.553927  0.810607  
Gr Liv Area           0.315723       0.261861  0.742061  
Garage Cars           0.433307       0.562320  0.634497  
Garage Area           0.364369       0.536310  0.617151  
Total Bsmt SF         0.265506       0.347908  0.664047  
1st Flr SF            0.236692       0.259898  0.646843  
Full Bath             0.472537       0.498692  0.554453  
Year Built            0.616008       0.815615  0.546037  
Year Remod/Add        1.000000       0.644251  0.529477  
Garage Yr Blt         0.644251       1.000000  0.517973  
target                0.529477       0.517973  1.000000

In [50]:
train.head()

Overall Qual  Gr Liv Area Exter Qual  Garage Cars  Garage Area  \
0            10         2392         Ex            3          968   
1             7         1352         Gd            2          466   
2             5          900         TA            1          288   
3             5         1174         TA            2          576   
4             7         1958         Gd            3          936   

  Kitchen Qual  Total Bsmt SF  1st Flr SF Bsmt Qual  Full Bath  Year Built  \
0           Ex           2392        2392        Ex          2        2003   
1           Gd           1352        1352        Ex          2        2006   
2           TA            864         900        TA          1        1967   
3           Gd            680         680        TA          1        1900   
4           Gd           1026        1026        Gd          2        2005   

   Year Remod/Add  Garage Yr Blt  target  
0            2003           2003  386250  
1            2007           2006  194000  
2            1967           1967  123000  
3            2006           2000  135000  
4            2005           2005  250000

In [51]:
# mapping encoding
categorical_qual_map = {
    'Po': 0,
    'Fa': 1,
    'TA': 2,
    'Gd': 3,
    'Ex': 4
}

train['Exter Qual'] = train['Exter Qual'].map(categorical_qual_map)
train['Kitchen Qual'] = train['Kitchen Qual'].map(categorical_qual_map)
train['Bsmt Qual'] = train['Bsmt Qual'].map(categorical_qual_map)
df.head()

Overall Qual  Gr Liv Area  Exter Qual  Garage Cars  Garage Area  \
0            10         2392           4            3          968   
1             7         1352           3            2          466   
2             5          900           2            1          288   
3             5         1174           2            2          576   
4             7         1958           3            3          936   

   Kitchen Qual  Total Bsmt SF  1st Flr SF  Bsmt Qual  Full Bath  Year Built  \
0             4           2392        2392          4          2        2003   
1             3           1352        1352          4          2        2006   
2             2            864         900          2          1        1967   
3             3            680         680          2          1        1900   
4             3           1026        1026          3          2        2005   

   Year Remod/Add  Garage Yr Blt  target  
0            2003           2003  386250  
1            2007           2006  194000  
2            1967           1967  123000  
3            2006           2000  135000  
4            2005           2005  250000

In [52]:
train[train['Garage Yr Blt']==2207].index

Int64Index([254], dtype='int64')

In [53]:
train.drop(train[train['Garage Yr Blt']==2207].index, inplace=True)
train.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 1349 entries, 0 to 1349
Data columns (total 14 columns):
 #   Column          Non-Null Count  Dtype
---  ------          --------------  -----
 0   Overall Qual    1349 non-null   int64
 1   Gr Liv Area     1349 non-null   int64
 2   Exter Qual      1349 non-null   int64
 3   Garage Cars     1349 non-null   int64
 4   Garage Area     1349 non-null   int64
 5   Kitchen Qual    1349 non-null   int64
 6   Total Bsmt SF   1349 non-null   int64
 7   1st Flr SF      1349 non-null   int64
 8   Bsmt Qual       1349 non-null   int64
 9   Full Bath       1349 non-null   int64
 10  Year Built      1349 non-null   int64
 11  Year Remod/Add  1349 non-null   int64
 12  Garage Yr Blt   1349 non-null   int64
 13  target          1349 non-null   int64
dtypes: int64(14)
memory usage: 158.1 KB


In [54]:
# 중복 행 제거
train.drop_duplicates(inplace=True)
train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1348 entries, 0 to 1349
Data columns (total 14 columns):
 #   Column          Non-Null Count  Dtype
---  ------          --------------  -----
 0   Overall Qual    1348 non-null   int64
 1   Gr Liv Area     1348 non-null   int64
 2   Exter Qual      1348 non-null   int64
 3   Garage Cars     1348 non-null   int64
 4   Garage Area     1348 non-null   int64
 5   Kitchen Qual    1348 non-null   int64
 6   Total Bsmt SF   1348 non-null   int64
 7   1st Flr SF      1348 non-null   int64
 8   Bsmt Qual       1348 non-null   int64
 9   Full Bath       1348 non-null   int64
 10  Year Built      1348 non-null   int64
 11  Year Remod/Add  1348 non-null   int64
 12  Garage Yr Blt   1348 non-null   int64
 13  target          1348 non-null   int64
dtypes: int64(14)
memory usage: 158.0 KB


In [37]:
train.shape

(1348, 14)

In [55]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error , r2_score # metrics = 평가지표

# feature, target 데이터 분리
y_target = train['target']
X_data = train.drop(['target'], axis=1, inplace=False)

# train, test 데이터 분리
X_train , X_test , y_train , y_test = train_test_split(X_data , y_target ,test_size=0.3, random_state=156)

# Linear Regression 
lr = LinearRegression()

# 학습
lr.fit(X_train , y_train )

# 예측
y_preds = lr.predict(X_test)

# 평가
mse = mean_squared_error(y_test, y_preds)
rmse = np.sqrt(mse)

print('MSE : {0:.3f} , RMSE : {1:.3F}'.format(mse , rmse))
print('Variance score : {0:.3f}'.format(r2_score(y_test, y_preds)))

MSE : 856383516.924 , RMSE : 29264.031
Variance score : 0.855


In [ ]:
pwd

'c:\\Users\\Jay\\Desktop\\dacon\\housing'

In [70]:
test = pd.read_csv('test.csv', encoding='utf-8-sig')
test = test.drop('id', axis=1)
print(test.shape)
test.head(3)

(1350, 13)


Overall Qual  Gr Liv Area Exter Qual  Garage Cars  Garage Area  \
0             9         1800         Gd            2          702   
1             6         1082         TA            1          240   
2             6         1573         Gd            2          440   

  Kitchen Qual  Total Bsmt SF  1st Flr SF Bsmt Qual  Full Bath  Year Built  \
0           Ex           1800        1800        Ex          2        2007   
1           TA           1082        1082        TA          1        1948   
2           Gd            756         769        Gd          2        2000   

   Year Remod/Add  Garage Yr Blt  
0            2007           2007  
1            1950           1948  
2            2000           2000

In [72]:
test['Exter Qual'] = test['Exter Qual'].map(categorical_qual_map)
test['Kitchen Qual'] = test['Kitchen Qual'].map(categorical_qual_map)
test['Bsmt Qual'] = test['Bsmt Qual'].map(categorical_qual_map)

In [73]:
test

Overall Qual  Gr Liv Area  Exter Qual  Garage Cars  Garage Area  \
0                9         1800           3            2          702   
1                6         1082           2            1          240   
2                6         1573           3            2          440   
3                6         2443           3            3          744   
4                5         1040           2            2          686   
...            ...          ...         ...          ...          ...   
1345             8         1932           4            3          774   
1346             5          912           2            1          288   
1347             4          861           2            2          288   
1348             5         1430           2            2          624   
1349             5         2337           2            2          560   

      Kitchen Qual  Total Bsmt SF  1st Flr SF  Bsmt Qual  Full Bath  \
0                4           1800        1800          4          2   
1                2           1082        1082          2          1   
2                3            756         769          3          2   
3                3           1158        1158          3          2   
4                2           1040        1040          2          1   
...            ...            ...         ...        ...        ...   
1345             4           1932        1932          4          2   
1346             2            912         912          2          1   
1347             2            861         861          1          1   
1348             3           1430        1430          4          2   
1349             2            662        1422          2          2   

      Year Built  Year Remod/Add  Garage Yr Blt  
0           2007            2007           2007  
1           1948            1950           1948  
2           2000            2000           2000  
3           2004            2004           2004  
4           1968            1968           1991  
...          ...             ...            ...  
1345        2008            2008           2008  
1346        1964            1964           1964  
1347        1920            1950           1920  
1348        2004            2005           2004  
1349        1900            1950           1945  

[1350 rows x 13 columns]

In [74]:
# 타겟 생성
predsTest = lr.predict(test)

In [75]:
submission = pd.read_csv("sample_submission.csv")
submission.head()

id  target
0   1       0
1   2       0
2   3       0
3   4       0
4   5       0

In [80]:
submission['target'] = predsTest
submission.head()

id         target
0   1  323913.013805
1   2  133117.823844
2   3  180119.546100
3   4  266621.118467
4   5  127109.648370

In [81]:
submission.to_csv("housing_linear.csv",index=False)

In [83]:
from pycaret.regression import *
reg = setup(data = train, target = 'target', normalize = True, session_id = 0, fold_shuffle=True )

AttributeError: 'Simple_Imputer' object has no attribute 'fill_value_categorical'

In [84]:
best = compare_models(sort= 'RMSE', n_select=3)

In [85]:
blend = blend_models(estimator_list= best, fold=5, optimize='RMSE') #voting regressor로 블렌딩합니다.
pred_holdout = predict_model(blend)

In [86]:
final_model = finalize_model(blend)
pred= predict_model(final_model, test)

In [87]:
pred['Label'].head()

0    351176.468750
1    127904.346354
2    177962.354167
3    264181.354167
4    130627.544271
Name: Label, dtype: float64

In [89]:
submission = pd.read_csv("sample_submission.csv")
submission.head()

id  target
0   1       0
1   2       0
2   3       0
3   4       0
4   5       0

In [90]:
submission['target'] = pred['Label']
submission.head()

id         target
0   1  351176.468750
1   2  127904.346354
2   3  177962.354167
3   4  264181.354167
4   5  130627.544271

In [91]:
submission.to_csv("housing_pycarot.csv",index=False)